# sample.ipynb

This notebook is a short example of how the MagicHour pipeline works. The code was taken from the main() function in sample_driver.py. Each section in this notebook describes a separate step in the pipeline that we use to process log files. The functions that are used here are intermediate driver functions that use the underlying MagicHour API. (The driver functions provide logging and measurements of function execution time.)

In [1]:
from magichour.api.local.sample.sample_driver import *

log_file = "tbird.log.500k"
transforms_file = "simpleTrans" 

read_lines_args = [0, 10]
read_lines_kwargs = {"skip_num_chars": 22}

logcluster_kwargs = {"support": "50"}

window_size = 60

paris_kwargs = {"r_slack": None}
fp_growth_kwargs = {"min_support": 0.005, "iterations": 10000} # only return 10000 itemsets...iterations = -1 will return all

---

# Preprocess

The preprocess step takes a log file and transforms it into an iterable of LogLine named tuples. While it is possible to do this without altering the original line via the get_lines() function in templates/templates.py, it is suggested that you write some transforms (see code below) and use the get_transformed_lines() function in order to perform normalizations like converting instances of things like machine/user names or IP addresses to standard tokens. Doing this will produce much better results in the Template step. We maintain the replacements in the LogLine named tuple in order to provide the ability to reconstruct LogLines throughout the pipeline.

Calculate transformed loglines from a log file+transform file.

In [ ]:
loglines = preprocess_step(log_file, transforms_file, *read_lines_args, **read_lines_kwargs)
write_pickle_file(loglines, transformed_lines_file)

2016-01-28 16:03:33,060 [INFO] [magichour.api.local.sample.sample_driver] Reading transforms from file: simpleTrans
2016-01-28 16:03:33,061 [INFO] [magichour.api.local.sample.sample_driver] Time in read_transforms_substep(): 0.000910997390747 seconds
2016-01-28 16:03:33,062 [INFO] [magichour.api.local.sample.sample_driver] Reading log lines from file: tbird.log.500k
2016-01-28 16:03:33,062 [INFO] [magichour.api.local.sample.sample_driver] Time in read_lines_substep(): 0.00056004524231 seconds
2016-01-28 16:03:33,063 [INFO] [magichour.api.local.sample.sample_driver] Transforming log lines...
2016-01-28 16:03:33,064 [INFO] [magichour.api.local.sample.sample_driver] Time in transformed_lines_substep(): 0.000664949417114 seconds


Read transformed loglines from a prepared pickle file.

In [24]:
loglines = read_pickle_file(transformed_lines_file)

2016-01-29 08:59:10,088 [INFO] [magichour.api.local.sample.sample_driver] Reading pickle file: transformed_lines.pickle
2016-01-29 08:59:39,506 [INFO] [magichour.api.local.sample.sample_driver] Time in read_pickle_file(): 29.4201660156 seconds


You can examine and play around with the loglines output in the cell below.

In [3]:
loglines[0]

LogLine(ts=1131523501.0, text='USER AFILE[INT]: tftp: client does not accept options', processed=None, replacements={'INT': ['14620'], 'AFILE': ['in.tftpd'], 'USER': ['aadmin1']}, supportId=None)

---

# Template

The template step takes in an iterable of LogLine named tuples and produces an iterable of Template named tuples. Ideally, this is the output of the previous preprocess step, however, these functions can be run independently as long as you marshal your data into iterable LogLines. In fact, the MagicHour API was designed with this in mind since we anticipate that users will want to mix and match different pipeline modules.

We provide two possible templating algorithms: LogCluster and StringMatch. Additional details about LogCluster is  available at http://ristov.github.io/logcluster/. For additional details about StringMatch, see the paper "[One Graph Is Worth a Thousand Logs: Uncovering Hidden Structures in Massive System Event Logs](http://link.springer.com/chapter/10.1007%2F978-3-642-04180-8_32)" by Aharon, Barash, Cohen, and Mordechai. There is also a [video available](http://videolectures.net/ecmlpkdd09_barash_gwtluhsmsel/) that provides more information about StringMatch.

*Note: The name "StringMatch" was taken from another [paper](http://users.cis.fiu.edu/~taoli/pub/liang-cikm2011.pdf) (Aharon et al do not name their algorithm).*

### LogCluster

Generate templates using the LogCluster algorithm.

In [25]:
gen_templates = template_step(loglines, "logcluster", **logcluster_kwargs)
write_pickle_file(gen_templates, template_file)

2016-01-29 08:59:39,998 [INFO] [magichour.api.local.sample.sample_driver] Running template_algorithm logcluster on log lines...
2016-01-29 08:59:39,998 [INFO] [magichour.api.local.sample.sample_driver] Running logcluster... ({'support': '50'})
2016-01-29 08:59:40,003 [INFO] [magichour.api.local.templates.templates] Writing lines to temporary file: /var/folders/00/24gqj0vd2_52cqll1jf07zpr0000gq/T/tmpLXBLEu
2016-01-29 08:59:40,499 [INFO] [magichour.api.local.templates.LogCluster] Calling subprocess: ['perl', '/Users/kylez/lab41/magichour/magichour/magichour/lib/LogCluster/logcluster-0.03/logcluster.pl', '--input', '/var/folders/00/24gqj0vd2_52cqll1jf07zpr0000gq/T/tmpLXBLEu', '--support', '50']
2016-01-29 08:59:56,314 [INFO] [magichour.api.local.templates.LogCluster] Fri Jan 29 08:59:40 2016: Starting the clustering process...
2016-01-29 08:59:56,315 [INFO] [magichour.api.local.templates.LogCluster] Fri Jan 29 08:59:46 2016: Total number of frequent words: 1420
2016-01-29 08:59:56,316 [IN

### **(\*\*WIP\*\*)** StringMatch

Generate tempaltes using the StringMatch algorithm. StringMatch uses cosine similarity to group lines which are alike. You should use LogCluster if you aren't tolerant of lossy templating. The preprocess step should help to mitigate the loss from StringMatch though.

In [ ]:
gen_templates = template_step(loglines, "stringmatch")
write_pickle_file(gen_templates, template_file)

Read templates from a prepared pickle file.

In [16]:
gen_templates = read_pickle_file(template_file)

2016-02-01 12:53:03,499 [INFO] [magichour.api.local.sample.sample_driver] Reading pickle file: templates.pickle
2016-02-01 12:53:03,681 [INFO] [magichour.api.local.logging_util] Time in read_pickle_file(): 0.182016849518 seconds


You can examine and play around with the templates output in the cell below.

In [12]:
gen_templates[75]

Template(id=462, match=<_sre.SRE_Pattern object at 0x7f9dcb11bc00>, str='MACHINENAME smartd[INT]: Device: FILEPATH Bad IEC (SMART) mode page, KEYVALUE, skip device')

---

# Apply Templates

The apply templates step takes in an iterable of LogLine named tuples and an iterable of Template named tuples (i.e. output of previous templating step). In this instance, we are applying the generated templates on the same log file that they came from. We believe that both this step and the Apply Events step (further down) are the only two steps that are needed to be implemented in a streaming fashion (to be able to keep up with log file ingest rates). The remainder of the steps described in this notebook could theoretically be run offline nightly (i.e. batch processing).

The output of the apply templates step is an iterable of TimedTemplate named tuples, representing the instances of each template that were found in the log file. If the template_id is -1 in a TimedTemplate, then that means that no template was found that matches that particular line.

Create timed templates by applying templates generated from the last step (Template) over an iterable of LogLines.

In [4]:
timed_templates = apply_templates_step(loglines, gen_templates)
write_pickle_file(timed_templates, timed_template_file)

2016-01-28 16:24:13,903 [INFO] [magichour.api.local.sample.sample_driver] Applying templates to lines...
2016-01-28 16:25:08,345 [INFO] [magichour.api.local.sample.sample_driver] Time in apply_templates_step(): 54.4422049522 seconds
2016-01-28 16:25:08,347 [INFO] [magichour.api.local.sample.sample_driver] Writing data to pickle file: timed_templates.pickle
2016-01-28 16:25:13,135 [INFO] [magichour.api.local.sample.sample_driver] Time in write_pickle_file(): 4.788449049 seconds


Read timed templates from a prepared pickle file.

In [3]:
timed_templates = read_pickle_file(timed_template_file)

2016-01-29 14:52:34,502 [INFO] [magichour.api.local.sample.sample_driver] Reading pickle file: timed_templates.pickle
2016-01-29 14:52:38,725 [INFO] [magichour.api.local.sample.sample_driver] Time in read_pickle_file(): 4.22322297096 seconds


You can examine and play around with the timed_templates output in the cell below.

In [15]:
timed_templates[0]

TimedTemplate(ts=1131523501.0, template_id=423)

---

# Window

The window step takes in an iterable of TimedTemplate named tuples (i.e. the output of the apply templates step) and returns an iterable of sets containing TimedTemplate instances. Each of these windows represent a time range in which the contained template_id's co-occurred. . In effect, we are creating transactions by grouping all TimedTemplates within *window_size*. These transactions will be passed to the next step which will perform market basket analysis on them in order to identify frequently co-occurring itemsets.

Create windows using timed templates generated from the last step (Apply Templates).

In [4]:
windows = window_step(timed_templates, window_size)
write_pickle_file(windows, window_file)

2016-01-29 14:52:38,729 [INFO] [magichour.api.local.sample.sample_driver] Creating windows from timed_templates...
2016-01-29 14:52:39,194 [INFO] [magichour.api.local.sample.sample_driver] Time in window_step(): 0.464958906174 seconds
2016-01-29 14:52:39,208 [INFO] [magichour.api.local.sample.sample_driver] Writing data to pickle file: windows.pickle
2016-01-29 14:52:44,288 [INFO] [magichour.api.local.sample.sample_driver] Time in write_pickle_file(): 5.0799870491 seconds


Read windows from a prepared pickle file.

In [2]:
windows = read_pickle_file(window_file)

2016-02-01 12:49:07,926 [INFO] [magichour.api.local.sample.sample_driver] Reading pickle file: windows.pickle
2016-02-01 12:49:11,915 [INFO] [magichour.api.local.logging_util] Time in read_pickle_file(): 3.98868513107 seconds


You can examine and play around with the window output in the cell below.

In [3]:
windows

[[TimedTemplate(ts=1131523501.0, template_id=423)],
 [TimedTemplate(ts=1131524071.0, template_id=157),
  TimedTemplate(ts=1131524073.0, template_id=157)],
 [TimedTemplate(ts=1131524106.0, template_id=157),
  TimedTemplate(ts=1131524107.0, template_id=157)],
 [TimedTemplate(ts=1131524196.0, template_id=157),
  TimedTemplate(ts=1131524197.0, template_id=157),
  TimedTemplate(ts=1131524199.0, template_id=157),
  TimedTemplate(ts=1131524201.0, template_id=157),
  TimedTemplate(ts=1131524202.0, template_id=157)],
 [TimedTemplate(ts=1131524287.0, template_id=157),
  TimedTemplate(ts=1131524290.0, template_id=157),
  TimedTemplate(ts=1131524290.0, template_id=157),
  TimedTemplate(ts=1131524291.0, template_id=157),
  TimedTemplate(ts=1131524292.0, template_id=157),
  TimedTemplate(ts=1131524292.0, template_id=157),
  TimedTemplate(ts=1131524293.0, template_id=157)],
 [TimedTemplate(ts=1131524400.0, template_id=157)],
 [TimedTemplate(ts=1131524901.0, template_id=423)],
 [TimedTemplate(ts=11315

In [4]:
len(windows)

1830

---

# Event Preprocess

In [3]:
from magichour.api.local.windows.util import *

In [4]:
windows = extract_template_ids(windows)

2016-02-01 12:49:14,094 [INFO] [magichour.api.local.logging_util] Time in extract_template_ids(): 0.107083082199 seconds


In [5]:
windows = remove_junk_drawer(windows)

2016-02-01 12:49:14,289 [INFO] [magichour.api.local.logging_util] Time in remove_junk_drawer(): 0.0523490905762 seconds


In [6]:
windows = uniqify_windows(windows)

2016-02-01 12:49:14,817 [INFO] [magichour.api.local.logging_util] Time in uniqify_windows(): 0.0179660320282 seconds


In [7]:
TF_IDF_THRESHOLD = 0
windows = tf_idf_filter(windows, TF_IDF_THRESHOLD)

2016-02-01 12:49:21,799 [INFO] [magichour.api.local.logging_util] Time in tf_idf_filter(): 6.26178693771 seconds


In [8]:
len(windows)

1830

---

# **(\*\*WIP\*\*)** Event

### **(\*\*WIP\*\*)** fp_growth

Generate events by applying the fp_growth algorithm on windows created from last step (Window).

In [9]:
gen_events = event_step(windows, "fp_growth", **fp_growth_kwargs)
#write_pickle_file(gen_events, event_file)

2016-02-01 12:49:55,264 [INFO] [magichour.api.local.sample.sample_driver] Running event algorithm %s on windows...
2016-02-01 12:49:55,265 [INFO] [magichour.api.local.sample.sample_driver] Running fp_growth algorithm... ({'iterations': 10000, 'min_support': 0.005})
2016-02-01 12:49:55,265 [INFO] [magichour.api.local.events.events] Min support 0.5% of 1830: 10.0
2016-02-01 12:49:59,353 [INFO] [magichour.api.local.logging_util] Time in fp_growth_substep(): 4.088285923 seconds
2016-02-01 12:49:59,354 [INFO] [magichour.api.local.logging_util] Time in event_step(): 4.0894639492 seconds


### **(\*\*WIP\*\*)** PARIS

Generate events by applying the PARIS algorithm on windows created from last step (Window).

In [ ]:
gen_events = event_step(windows, "paris", **paris_kwargs)
write_pickle_file(gen_events, event_file)

Read events from a prepared pickle file.

In [12]:
gen_events = read_pickle_file(event_file)

2016-01-29 16:29:37,341 [INFO] [magichour.api.local.sample.sample_driver] Reading pickle file: events.pickle
2016-01-29 16:29:37,343 [INFO] [magichour.api.local.sample.sample_driver] Time in read_pickle_file(): 0.00146198272705 seconds


**(\*\*WIP\*\*)** You can examine and play around with the event output in the cell below.

In [10]:
gen_events

[frozenset({6}),
 frozenset({6, 23}),
 frozenset({6, 23, 197}),
 frozenset({6, 23, 334}),
 frozenset({6, 23, 197, 334}),
 frozenset({6, 23, 376}),
 frozenset({6, 23, 197, 376}),
 frozenset({6, 23, 334, 376}),
 frozenset({6, 23, 197, 334, 376}),
 frozenset({6, 25}),
 frozenset({6, 23, 25}),
 frozenset({6, 23, 25, 197}),
 frozenset({6, 23, 25, 334}),
 frozenset({6, 23, 25, 197, 334}),
 frozenset({6, 23, 25, 376}),
 frozenset({6, 23, 25, 197, 376}),
 frozenset({6, 23, 25, 334, 376}),
 frozenset({6, 23, 25, 197, 334, 376}),
 frozenset({6, 25, 56}),
 frozenset({6, 25, 56, 99}),
 frozenset({6, 25, 57}),
 frozenset({6, 25, 56, 57}),
 frozenset({6, 25, 56, 57, 99}),
 frozenset({6, 25, 57, 99}),
 frozenset({6, 25, 59}),
 frozenset({6, 23, 25, 59}),
 frozenset({6, 23, 25, 59, 197}),
 frozenset({6, 23, 25, 59, 334}),
 frozenset({6, 23, 25, 59, 197, 334}),
 frozenset({6, 23, 25, 59, 376}),
 frozenset({6, 23, 25, 59, 197, 376}),
 frozenset({6, 23, 25, 59, 334, 376}),
 frozenset({6, 23, 25, 59, 197,

In [11]:
tfidf_gen_events = tf_idf_filter(gen_events, 2)
gen_events = tfidf_gen_events

2016-02-01 12:52:08,088 [INFO] [magichour.api.local.logging_util] Time in tf_idf_filter(): 2.0 minutes, 2.07430815697 seconds


In [13]:
gen_events

[[],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [56],
 [56],
 [57],
 [56, 57],
 [56, 57],
 [57],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],


In [14]:
from magichour.api.local.events.util import get_longest_sets_possible

gen_events = [frozenset(sorted(event)) for event in gen_events if event]
gen_events = list(get_longest_sets_possible(gen_events))

2016-02-01 12:52:48,092 [INFO] [magichour.api.local.logging_util] Time in get_longest_sets_possible(): 0.000552177429199 seconds


In [17]:
template_d = {template_id : template for (template_id, template) in [(template.id, template) for template in gen_templates]}

In [18]:
e = []
for s in gen_events:
    ts = []
    for elem in s:
        ts.append("%s: %s" % (elem, template_d[elem].str))
    e.append(ts)

In [19]:
gen_events

[frozenset({56, 57, 61, 62, 98}), frozenset({413})]

In [20]:
e

[['56: USERINT dhcpd: DHCPOFFER on IPADDR to MACADDR via ethINT',
  '57: USERINT dhcpd: DHCPDISCOVER from MACADDR via ethINT',
  '98: USERINT dhcpd: DHCPREQUEST for IPADDR (IPADDR) from MACADDR via ethINT: unknown lease IPADDR.',
  '61: USERINT dhcpd: DHCPREQUEST for IPADDR (IPADDR) from MACADDR via ethINT',
  '62: USERINT dhcpd: DHCPACK on IPADDR to MACADDR via ethINT'],
 ['413: USERINT sshd[INT]: Accepted publickey for USER from ::ffff:IPADDR port INT sshINT']]

---

# **(\*\*WIP\*\*)** Apply Events

In [ ]:
# TODO